In [1]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))
import pandas as pd
import numpy as np
import io
import random
import math
import scipy.stats
import matplotlib.pylab as plt

C:\Users\devin\AppData\Local\Temp\ipykernel_15152\621582838.py:1: DeprecationWarning: Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython display
  from IPython.core.display import display, HTML


In [2]:
# Initialize year variable
year = 2023 #(2019, 2021, 2022, 2023)

In [3]:
# Read in data based on the year
if year == 2019:
    data = pd.read_csv('data/18_19tourneycs.csv')
elif year == 2021:
    data = pd.read_csv('data/20_21tourneycs.csv')
elif year == 2022:
    data = pd.read_csv('data/21_22tourneycs.csv')
elif year == 2023:
    data = pd.read_csv('data/22_23tourneycs.csv')
data.head()

Region  Seed         School    SRS
0       1     1        Alabama  23.19
1       1    16   Texas A&M-CC  -2.57
2       1     8       Maryland  14.58
3       1     9  West Virginia  15.95
4       1     4       Virginia  13.28

In [4]:
# Rename columns of data DataFrame
data.columns = ['Region', 'Seed', 'Team', 'SRS']
data

Region  Seed           Team    SRS
0        1     1        Alabama  23.19
1        1    16   Texas A&M-CC  -2.57
2        1     8       Maryland  14.58
3        1     9  West Virginia  15.95
4        1     4       Virginia  13.28
..     ...   ...            ...    ...
59       4    11  Arizona State  11.29
60       4     7   Northwestern  13.68
61       4    10    Boise State  12.78
62       4     2           UCLA  22.11
63       4    15  UNC Asheville  -1.74

[64 rows x 4 columns]

In [5]:
num_of_sims = 1000  # Number of simulations
teams = data.to_numpy().tolist()  # Convert DataFrame to a nested list
team_dict = {}  # Dictionary to store team data

# Iterate through each team
for i in range(0, len(teams)):
    # Initialize an empty list for each team in the team_dict
    team_dict[teams[i][2]] = [0, 0, 0, 0, 0, 0, 0]
    # The team name is accessed using teams[i][2], assuming the team name is in the third column of the data

In [6]:
"""
Given a list of teams in a specific round and the round number,
find_winners randomly determines the winners of each matchup based on the
SRS difference between the teams and returns a list of the winners
"""
def find_winners(input_list, round):

    winners = []

    # Iterate over the input list of teams
    for i in range(0, len(input_list)):
        # Skips if the index is odd (represents the second team in a matchup)
        if i % 2 != 0:
            pass
        else:
            # Get the first team and the second team in the matchup
            team1 = input_list[i]
            team2 = input_list[i+1]

            # Calculate the SRS difference between the teams
            srs_diff = team1[3] - team2[3]

            # Calculate the win probability of Team 1 using the SRS difference
            team1_prob = scipy.stats.norm(0, 10.36).cdf(srs_diff)

            # Generate a random draw between 0 and 1
            draw = random.random()

            # Determine the winner based on the draw and win probability
            if draw <= team1_prob:
                # Team 1 wins
                winners.append(team1)
                team_dict[team1[2]][round] += 1
            else:
                # Team 2 wins
                winners.append(team2)
                team_dict[team2[2]][round] += 1

    return winners


In [7]:
"""
Prints out the bracket representation of the tournament rounds
based on the provided round_list
"""
def bracket_printout(round_list):

    for i in range(0, len(round_list)):
        temp_list = round_list[i]

        # Iterate over the matchups in the current round
        for j in range(0, len(temp_list)):
            # Print the team seed, name, and SRS for each matchup
            print(str(temp_list[j][1]) + " " + temp_list[j][2] + " " + str(temp_list[j][3]))

            # Print an empty line after every even-indexed matchup
            if j % 2 != 0:
                print("")

        # Print empty lines between each round
        print("")
        print("")
        print("")


In [8]:
"""
Simulates a tournament by finding winners in each round and printing the bracket
"""
def tourney_sim(teams):
    # Increment the count of tournaments for each team
    for x in team_dict:
        team_dict[x][0] += 1

    # Find winners in the Round of 64
    round_32 = find_winners(teams, 1)

    # Find winners in the Round of 32
    sweet_16 = find_winners(round_32, 2)

    # Find winners in the Sweet 16
    elite_8 = find_winners(sweet_16, 3)

    # Find winners in the Elite 8
    final_4 = find_winners(elite_8, 4)

    # Find winners in the Final 4
    championship = find_winners(final_4, 5)

    # Find the winner in the Championship
    winner = find_winners(championship, 6)

    # Print the bracket for all rounds
    # Uncomment below to see bracket format of simulation. Heads up: it is a lot of output!
    bracket_printout([teams, round_32, sweet_16, elite_8, final_4, championship, winner])


In [9]:
%%time
# Run the monte-carlo tournament simulation
for i in range(1, num_of_sims+1):
    tourney_sim(teams)

# Calculate the average statistics for each team
for x in team_dict:
    # Divide the count of wins in each round by the total number of simulations
    for i in range(0, len(team_dict[x])):
        team_dict[x][i] = team_dict[x][i] / num_of_sims

    # Print the team name and its average statistics
    print(x + " " + str(team_dict[x]))


1 Alabama 23.19
16 Texas A&M-CC -2.57

8 Maryland 14.58
9 West Virginia 15.95

4 Virginia 13.28
13 Furman 4.89

5 San Diego State 15.81
12 College of Charleston 8.4

3 Baylor 17.3
14 UC Santa Barbara 3.3

6 Creighton 17.83
11 NC State 12.5

7 Missouri 11.41
10 Utah State 14.23

2 Arizona 19.08
15 Princeton 4.76

1 Purdue 18.23
16 Fairleigh Dickinson -8.98

8 Memphis 14.5
9 Florida Atlantic 13.92

4 Tennessee 20.84
13 Louisiana 4.27

5 Duke 15.83
12 Oral Roberts 8.55

3 Kansas State 15.79
14 Montana State 2.18

6 Kentucky 14.76
11 Providence 12.89

7 Michigan State 14.25
10 USC 13.06

2 Marquette 17.07
15 Vermont 1.63

1 Houston 22.2
16 Northern Kentucky -0.83

8 Iowa 14.08
9 Auburn 14.35

4 Indiana 14.94
13 Kent State 7.53

5 Miami 13.98
12 Drake 7.84

3 Xavier 16.03
14 Kennesaw State 0.6

6 Iowa State 15.36
11 Pittsburgh 10.59

7 Texas A&M 13.76
10 Penn State 13.04

2 Texas 20.56
15 Colgate 2.2

1 Kansas 19.2
16 Howard -5.04

8 Arkansas 15.99
9 Illinois 14.81

4 Uconn 22.95
13 Iona 7.

1 Alabama 23.19
16 Texas A&M-CC -2.57

8 Maryland 14.58
9 West Virginia 15.95

4 Virginia 13.28
13 Furman 4.89

5 San Diego State 15.81
12 College of Charleston 8.4

3 Baylor 17.3
14 UC Santa Barbara 3.3

6 Creighton 17.83
11 NC State 12.5

7 Missouri 11.41
10 Utah State 14.23

2 Arizona 19.08
15 Princeton 4.76

1 Purdue 18.23
16 Fairleigh Dickinson -8.98

8 Memphis 14.5
9 Florida Atlantic 13.92

4 Tennessee 20.84
13 Louisiana 4.27

5 Duke 15.83
12 Oral Roberts 8.55

3 Kansas State 15.79
14 Montana State 2.18

6 Kentucky 14.76
11 Providence 12.89

7 Michigan State 14.25
10 USC 13.06

2 Marquette 17.07
15 Vermont 1.63

1 Houston 22.2
16 Northern Kentucky -0.83

8 Iowa 14.08
9 Auburn 14.35

4 Indiana 14.94
13 Kent State 7.53

5 Miami 13.98
12 Drake 7.84

3 Xavier 16.03
14 Kennesaw State 0.6

6 Iowa State 15.36
11 Pittsburgh 10.59

7 Texas A&M 13.76
10 Penn State 13.04

2 Texas 20.56
15 Colgate 2.2

1 Kansas 19.2
16 Howard -5.04

8 Arkansas 15.99
9 Illinois 14.81

4 Uconn 22.95
13 Iona 7.

1 Alabama 23.19
16 Texas A&M-CC -2.57

8 Maryland 14.58
9 West Virginia 15.95

4 Virginia 13.28
13 Furman 4.89

5 San Diego State 15.81
12 College of Charleston 8.4

3 Baylor 17.3
14 UC Santa Barbara 3.3

6 Creighton 17.83
11 NC State 12.5

7 Missouri 11.41
10 Utah State 14.23

2 Arizona 19.08
15 Princeton 4.76

1 Purdue 18.23
16 Fairleigh Dickinson -8.98

8 Memphis 14.5
9 Florida Atlantic 13.92

4 Tennessee 20.84
13 Louisiana 4.27

5 Duke 15.83
12 Oral Roberts 8.55

3 Kansas State 15.79
14 Montana State 2.18

6 Kentucky 14.76
11 Providence 12.89

7 Michigan State 14.25
10 USC 13.06

2 Marquette 17.07
15 Vermont 1.63

1 Houston 22.2
16 Northern Kentucky -0.83

8 Iowa 14.08
9 Auburn 14.35

4 Indiana 14.94
13 Kent State 7.53

5 Miami 13.98
12 Drake 7.84

3 Xavier 16.03
14 Kennesaw State 0.6

6 Iowa State 15.36
11 Pittsburgh 10.59

7 Texas A&M 13.76
10 Penn State 13.04

2 Texas 20.56
15 Colgate 2.2

1 Kansas 19.2
16 Howard -5.04

8 Arkansas 15.99
9 Illinois 14.81

4 Uconn 22.95
13 Iona 7.

1 Alabama 23.19
16 Texas A&M-CC -2.57

8 Maryland 14.58
9 West Virginia 15.95

4 Virginia 13.28
13 Furman 4.89

5 San Diego State 15.81
12 College of Charleston 8.4

3 Baylor 17.3
14 UC Santa Barbara 3.3

6 Creighton 17.83
11 NC State 12.5

7 Missouri 11.41
10 Utah State 14.23

2 Arizona 19.08
15 Princeton 4.76

1 Purdue 18.23
16 Fairleigh Dickinson -8.98

8 Memphis 14.5
9 Florida Atlantic 13.92

4 Tennessee 20.84
13 Louisiana 4.27

5 Duke 15.83
12 Oral Roberts 8.55

3 Kansas State 15.79
14 Montana State 2.18

6 Kentucky 14.76
11 Providence 12.89

7 Michigan State 14.25
10 USC 13.06

2 Marquette 17.07
15 Vermont 1.63

1 Houston 22.2
16 Northern Kentucky -0.83

8 Iowa 14.08
9 Auburn 14.35

4 Indiana 14.94
13 Kent State 7.53

5 Miami 13.98
12 Drake 7.84

3 Xavier 16.03
14 Kennesaw State 0.6

6 Iowa State 15.36
11 Pittsburgh 10.59

7 Texas A&M 13.76
10 Penn State 13.04

2 Texas 20.56
15 Colgate 2.2

1 Kansas 19.2
16 Howard -5.04

8 Arkansas 15.99
9 Illinois 14.81

4 Uconn 22.95
13 Iona 7.

1 Alabama 23.19
16 Texas A&M-CC -2.57

8 Maryland 14.58
9 West Virginia 15.95

4 Virginia 13.28
13 Furman 4.89

5 San Diego State 15.81
12 College of Charleston 8.4

3 Baylor 17.3
14 UC Santa Barbara 3.3

6 Creighton 17.83
11 NC State 12.5

7 Missouri 11.41
10 Utah State 14.23

2 Arizona 19.08
15 Princeton 4.76

1 Purdue 18.23
16 Fairleigh Dickinson -8.98

8 Memphis 14.5
9 Florida Atlantic 13.92

4 Tennessee 20.84
13 Louisiana 4.27

5 Duke 15.83
12 Oral Roberts 8.55

3 Kansas State 15.79
14 Montana State 2.18

6 Kentucky 14.76
11 Providence 12.89

7 Michigan State 14.25
10 USC 13.06

2 Marquette 17.07
15 Vermont 1.63

1 Houston 22.2
16 Northern Kentucky -0.83

8 Iowa 14.08
9 Auburn 14.35

4 Indiana 14.94
13 Kent State 7.53

5 Miami 13.98
12 Drake 7.84

3 Xavier 16.03
14 Kennesaw State 0.6

6 Iowa State 15.36
11 Pittsburgh 10.59

7 Texas A&M 13.76
10 Penn State 13.04

2 Texas 20.56
15 Colgate 2.2

1 Kansas 19.2
16 Howard -5.04

8 Arkansas 15.99
9 Illinois 14.81

4 Uconn 22.95
13 Iona 7.

...

1 Alabama 23.19
16 Texas A&M-CC -2.57

8 Maryland 14.58
9 West Virginia 15.95

4 Virginia 13.28
13 Furman 4.89

5 San Diego State 15.81
12 College of Charleston 8.4

3 Baylor 17.3
14 UC Santa Barbara 3.3

6 Creighton 17.83
11 NC State 12.5

7 Missouri 11.41
10 Utah State 14.23

2 Arizona 19.08
15 Princeton 4.76

1 Purdue 18.23
16 Fairleigh Dickinson -8.98

8 Memphis 14.5
9 Florida Atlantic 13.92

4 Tennessee 20.84
13 Louisiana 4.27

5 Duke 15.83
12 Oral Roberts 8.55

3 Kansas State 15.79
14 Montana State 2.18

6 Kentucky 14.76
11 Providence 12.89

7 Michigan State 14.25
10 USC 13.06

2 Marquette 17.07
15 Vermont 1.63

1 Houston 22.2
16 Northern Kentucky -0.83

8 Iowa 14.08
9 Auburn 14.35

4 Indiana 14.94
13 Kent State 7.53

5 Miami 13.98
12 Drake 7.84

3 Xavier 16.03
14 Kennesaw State 0.6

6 Iowa State 15.36
11 Pittsburgh 10.59

7 Texas A&M 13.76
10 Penn State 13.04

2 Texas 20.56
15 Colgate 2.2

1 Kansas 19.2
16 Howard -5.04

8 Arkansas 15.99
9 Illinois 14.81

4 Uconn 22.95
13 Iona 7.

1 Alabama 23.19
16 Texas A&M-CC -2.57

8 Maryland 14.58
9 West Virginia 15.95

4 Virginia 13.28
13 Furman 4.89

5 San Diego State 15.81
12 College of Charleston 8.4

3 Baylor 17.3
14 UC Santa Barbara 3.3

6 Creighton 17.83
11 NC State 12.5

7 Missouri 11.41
10 Utah State 14.23

2 Arizona 19.08
15 Princeton 4.76

1 Purdue 18.23
16 Fairleigh Dickinson -8.98

8 Memphis 14.5
9 Florida Atlantic 13.92

4 Tennessee 20.84
13 Louisiana 4.27

5 Duke 15.83
12 Oral Roberts 8.55

3 Kansas State 15.79
14 Montana State 2.18

6 Kentucky 14.76
11 Providence 12.89

7 Michigan State 14.25
10 USC 13.06

2 Marquette 17.07
15 Vermont 1.63

1 Houston 22.2
16 Northern Kentucky -0.83

8 Iowa 14.08
9 Auburn 14.35

4 Indiana 14.94
13 Kent State 7.53

5 Miami 13.98
12 Drake 7.84

3 Xavier 16.03
14 Kennesaw State 0.6

6 Iowa State 15.36
11 Pittsburgh 10.59

7 Texas A&M 13.76
10 Penn State 13.04

2 Texas 20.56
15 Colgate 2.2

1 Kansas 19.2
16 Howard -5.04

8 Arkansas 15.99
9 Illinois 14.81

4 Uconn 22.95
13 Iona 7.

1 Alabama 23.19
16 Texas A&M-CC -2.57

8 Maryland 14.58
9 West Virginia 15.95

4 Virginia 13.28
13 Furman 4.89

5 San Diego State 15.81
12 College of Charleston 8.4

3 Baylor 17.3
14 UC Santa Barbara 3.3

6 Creighton 17.83
11 NC State 12.5

7 Missouri 11.41
10 Utah State 14.23

2 Arizona 19.08
15 Princeton 4.76

1 Purdue 18.23
16 Fairleigh Dickinson -8.98

8 Memphis 14.5
9 Florida Atlantic 13.92

4 Tennessee 20.84
13 Louisiana 4.27

5 Duke 15.83
12 Oral Roberts 8.55

3 Kansas State 15.79
14 Montana State 2.18

6 Kentucky 14.76
11 Providence 12.89

7 Michigan State 14.25
10 USC 13.06

2 Marquette 17.07
15 Vermont 1.63

1 Houston 22.2
16 Northern Kentucky -0.83

8 Iowa 14.08
9 Auburn 14.35

4 Indiana 14.94
13 Kent State 7.53

5 Miami 13.98
12 Drake 7.84

3 Xavier 16.03
14 Kennesaw State 0.6

6 Iowa State 15.36
11 Pittsburgh 10.59

7 Texas A&M 13.76
10 Penn State 13.04

2 Texas 20.56
15 Colgate 2.2

1 Kansas 19.2
16 Howard -5.04

8 Arkansas 15.99
9 Illinois 14.81

4 Uconn 22.95
13 Iona 7.

1 Alabama 23.19
16 Texas A&M-CC -2.57

8 Maryland 14.58
9 West Virginia 15.95

4 Virginia 13.28
13 Furman 4.89

5 San Diego State 15.81
12 College of Charleston 8.4

3 Baylor 17.3
14 UC Santa Barbara 3.3

6 Creighton 17.83
11 NC State 12.5

7 Missouri 11.41
10 Utah State 14.23

2 Arizona 19.08
15 Princeton 4.76

1 Purdue 18.23
16 Fairleigh Dickinson -8.98

8 Memphis 14.5
9 Florida Atlantic 13.92

4 Tennessee 20.84
13 Louisiana 4.27

5 Duke 15.83
12 Oral Roberts 8.55

3 Kansas State 15.79
14 Montana State 2.18

6 Kentucky 14.76
11 Providence 12.89

7 Michigan State 14.25
10 USC 13.06

2 Marquette 17.07
15 Vermont 1.63

1 Houston 22.2
16 Northern Kentucky -0.83

8 Iowa 14.08
9 Auburn 14.35

4 Indiana 14.94
13 Kent State 7.53

5 Miami 13.98
12 Drake 7.84

3 Xavier 16.03
14 Kennesaw State 0.6

6 Iowa State 15.36
11 Pittsburgh 10.59

7 Texas A&M 13.76
10 Penn State 13.04

2 Texas 20.56
15 Colgate 2.2

1 Kansas 19.2
16 Howard -5.04

8 Arkansas 15.99
9 Illinois 14.81

4 Uconn 22.95
13 Iona 7.

1 Alabama 23.19
16 Texas A&M-CC -2.57

8 Maryland 14.58
9 West Virginia 15.95

4 Virginia 13.28
13 Furman 4.89

5 San Diego State 15.81
12 College of Charleston 8.4

3 Baylor 17.3
14 UC Santa Barbara 3.3

6 Creighton 17.83
11 NC State 12.5

7 Missouri 11.41
10 Utah State 14.23

2 Arizona 19.08
15 Princeton 4.76

1 Purdue 18.23
16 Fairleigh Dickinson -8.98

8 Memphis 14.5
9 Florida Atlantic 13.92

4 Tennessee 20.84
13 Louisiana 4.27

5 Duke 15.83
12 Oral Roberts 8.55

3 Kansas State 15.79
14 Montana State 2.18

6 Kentucky 14.76
11 Providence 12.89

7 Michigan State 14.25
10 USC 13.06

2 Marquette 17.07
15 Vermont 1.63

1 Houston 22.2
16 Northern Kentucky -0.83

8 Iowa 14.08
9 Auburn 14.35

4 Indiana 14.94
13 Kent State 7.53

5 Miami 13.98
12 Drake 7.84

3 Xavier 16.03
14 Kennesaw State 0.6

6 Iowa State 15.36
11 Pittsburgh 10.59

7 Texas A&M 13.76
10 Penn State 13.04

2 Texas 20.56
15 Colgate 2.2

1 Kansas 19.2
16 Howard -5.04

8 Arkansas 15.99
9 Illinois 14.81

4 Uconn 22.95
13 Iona 7.

In [10]:
point_system = [0, 1, 2, 3, 5, 8, 13]  # Predefined point system for each round

expected_values = {}  # Dictionary to store the expected value for each team

# Calculate the expected value for each team
for team, probabilities in team_dict.items():
    expected_value = sum(probabilities[i] * point_system[i] for i in range(len(probabilities)))
    expected_values[team] = expected_value

# Sort teams by expected value in descending order
sorted_teams = sorted(expected_values.items(), key=lambda x: x[1], reverse=True)

# Print the expected value for each team
for team, expected_value in sorted_teams:
    print(f"{team}: {expected_value:.3f}")

Alabama: 11.562
Houston: 10.129
UCLA: 9.001
Uconn: 8.123
Tennessee: 7.783
Texas: 7.198
Arizona: 5.615
Purdue: 5.171
Marquette: 4.565
Kansas: 4.538
Gonzaga: 4.417
Xavier: 3.590
Baylor: 3.588
Kansas State: 3.454
Creighton: 3.067
San Diego State: 2.722
Indiana: 2.469
Saint Mary's: 2.385
Duke: 2.295
Iowa State: 2.181
Virginia: 2.137
Kentucky: 2.002
Miami: 1.983
TCU: 1.798
Utah State: 1.631
Michigan State: 1.622
West Virginia: 1.408
Arkansas: 1.407
Memphis: 1.402
USC: 1.204
Florida Atlantic: 1.202
Providence: 1.180
Illinois: 1.129
Auburn: 1.051
Maryland: 1.014
Iowa: 1.012
Texas A&M: 1.004
Penn State: 1.002
Northwestern: 0.873
NC State: 0.862
Boise State: 0.797
Missouri: 0.720
Pittsburgh: 0.715
Arizona State: 0.654
Drake: 0.510
Kent State: 0.464
College of Charleston: 0.430
Furman: 0.362
Oral Roberts: 0.339
VCU: 0.308
Princeton: 0.154
Montana State: 0.130
UC Santa Barbara: 0.113
Iona: 0.107
Grand Canyon: 0.107
Kennesaw State: 0.091
Vermont: 0.072
Louisiana: 0.060
Colgate: 0.051
Northern Kent

In [11]:
# Convert dictionary to DataFrame
df_expected_values = pd.DataFrame.from_dict(expected_values, orient='index', columns=['Expected Value'])

# Sort teams by expected value in descending order
df_expected_values = df_expected_values.sort_values(by='Expected Value', ascending=False)

# Reset the index
df_expected_values = df_expected_values.reset_index().rename(columns={'index': 'Team'})

# Display the DataFrame
display(df_expected_values)

Team  Expected Value
0               Alabama          11.562
1               Houston          10.129
2                  UCLA           9.001
3                 Uconn           8.123
4             Tennessee           7.783
..                  ...             ...
59    Northern Kentucky           0.011
60        UNC Asheville           0.011
61               Howard           0.008
62         Texas A&M-CC           0.006
63  Fairleigh Dickinson           0.004

[64 rows x 2 columns]

In [12]:
# Merge the dataframes based on the 'Team' column
df_merged = data.merge(df_expected_values, on='Team')

# Display the merged DataFrame
df_merged.head()

Region  Seed           Team    SRS  Expected Value
0       1     1        Alabama  23.19          11.562
1       1    16   Texas A&M-CC  -2.57           0.006
2       1     8       Maryland  14.58           1.014
3       1     9  West Virginia  15.95           1.408
4       1     4       Virginia  13.28           2.137

In [13]:
# Define the mapping of seed values to cost values
seed_cost_mapping = {
    1: 75,
    2: 40,
    3: 25,
    4: 20,
    5: 17,
    6: 15,
    7: 12,
    8: 10,
    9: 9,
    10: 8,
    11: 7,
    12: 6,
    13: 5,
    14: 4,
    15: 3,
    16: 1,
}

# Add a new column 'Cost' to df_merged based on the 'Seed' column
df_merged['Cost'] = df_merged['Seed'].map(seed_cost_mapping)

# Display the merged DataFrame
df_merged.head()

Region  Seed           Team    SRS  Expected Value  Cost
0       1     1        Alabama  23.19          11.562    75
1       1    16   Texas A&M-CC  -2.57           0.006     1
2       1     8       Maryland  14.58           1.014    10
3       1     9  West Virginia  15.95           1.408     9
4       1     4       Virginia  13.28           2.137    20

In [14]:
# Define the knapsack function
def knapsack(items, budget):
    n = len(items)
    dp = [[0] * (budget + 1) for _ in range(n + 1)]

    for i in range(1, n + 1):
        for j in range(1, budget + 1):
            cost = items[i - 1]['Cost']
            value = items[i - 1]['Expected Value']
            if cost > j:
                dp[i][j] = dp[i - 1][j]
            else:
                dp[i][j] = max(dp[i - 1][j], value + dp[i - 1][j - cost])

    selected = []
    j = budget
    for i in range(n, 0, -1):
        if dp[i][j] != dp[i - 1][j]:
            selected.append(items[i - 1])
            j -= items[i - 1]['Cost']

    return selected

# Run the knapsack optimization on df_merged
selected_teams = knapsack(df_merged.to_dict('records'), budget=224)

# Create a new DataFrame for the selected teams
df_selected = pd.DataFrame(selected_teams)

# Display the selected teams and their information
display(df_selected)

# Calculate the total sum of the cost and expected value columns
total_cost = df_selected['Cost'].sum()
total_expected_value = df_selected['Expected Value'].sum()

# Print the total sums
print(f"Total Cost: {total_cost}")
print(f"Total Expected Value: {total_expected_value:.3f}")

Region  Seed             Team    SRS  Expected Value  Cost
0        4     2             UCLA  22.11           9.001    40
1        4     3          Gonzaga  18.99           4.417    25
2        4     4            Uconn  22.95           8.123    20
3        3     2            Texas  20.56           7.198    40
4        3     6       Iowa State  15.36           2.181    15
5        2    10              USC  13.06           1.204     8
6        2    11       Providence  12.89           1.180     7
7        2     4        Tennessee  20.84           7.783    20
8        1    10       Utah State  14.23           1.631     8
9        1     6        Creighton  17.83           3.067    15
10       1     5  San Diego State  15.81           2.722    17
11       1     9    West Virginia  15.95           1.408     9

Total Cost: 224
Total Expected Value: 49.915
